<a href="https://colab.research.google.com/github/nguyenanhtienabcd/AIO2024_EXERCISE/blob/feature%2FMODULE8-WEEK1/m08w01_ex02.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Named Entity Recognition

link để tham khảo thêm về tiêu chuẩn standoff: \
https://brat.nlplab.org/standoff.html

In [ ]:
!mkdir "/content/MACCROBAT2018"

In [ ]:
!unzip "/content/MACCROBAT2018.zip" -d "/content/MACCROBAT2018"

Archive:  /content/MACCROBAT2018.zip
  inflating: /content/MACCROBAT2018/15939911.ann  
  inflating: /content/MACCROBAT2018/15939911.txt  
  inflating: /content/MACCROBAT2018/16778410.ann  
  inflating: /content/MACCROBAT2018/16778410.txt  
  inflating: /content/MACCROBAT2018/17803823.ann  
  inflating: /content/MACCROBAT2018/17803823.txt  
  inflating: /content/MACCROBAT2018/18236639.ann  
  inflating: /content/MACCROBAT2018/18236639.txt  
  inflating: /content/MACCROBAT2018/18258107.ann  
  inflating: /content/MACCROBAT2018/18258107.txt  
  inflating: /content/MACCROBAT2018/18416479.ann  
  inflating: /content/MACCROBAT2018/18416479.txt  
  inflating: /content/MACCROBAT2018/18561524.ann  
  inflating: /content/MACCROBAT2018/18561524.txt  
  inflating: /content/MACCROBAT2018/18666334.ann  
  inflating: /content/MACCROBAT2018/18666334.txt  
  inflating: /content/MACCROBAT2018/18787726.ann  
  inflating: /content/MACCROBAT2018/18787726.txt  
  inflating: /content/MACCROBAT2018/18815636.

In [ ]:
import os
from  typing import List, Dict, Tuple

class Preprocessing_Maccrobat:
  def __init__(self, dataset_folder, tokenizer):
    # Tạo danh sách các ID file từ thư mục dữ liệu (chỉ lấy phần tên file không có đuôi).
    self.file_ids = [f.split(".")[0] for f in os.listdir(dataset_folder) if f.endswith(".txt")]

    # tách riêng các tên file thành các list khác nhau
    self.text_files = [f+".txt" for f in self.file_ids]
    self.ann_files = [f+".ann" for f in self.file_ids]

    # số lượng samples
    self.num_samples = len(self.file_ids)

    # chỉ định kiểu dữ liệu ban đầu. Nhất quán trong quá trình lập trình
    self.texts: List[str] = []

    # Đọc dữ liệu từ các file
    for i in range(self.num_samples):
      file_path = os.path.join(dataset_folder, self.text_files[i])
      with open(file_path, "r") as f:
        self.texts.append(f.read())

    # tách dòng text thành các list
    self.tags: List[Dict[str, str]] = []
    for i in range(self.num_samples):
      file_path = os.path.join(dataset_folder, self.ann_files[i])
      with open (file_path, "r") as f:
        text_bound_ann = [t.split("\t") for t in f.read().split("\n") if t.startswith("T")]

        # tách tiếp phần tử 1 trong list trên thành 1 list khác
        text_bound_lst = []
        for text_b in text_bound_ann:
          label = text_b[1].split(" ")
          try:
            _ = int(label[1])
            _ = int(label[2])
            tag = {
                "text": text_b[-1],
                "label": label[0],
                "start": label[1],
                "end": label[2],
            }
            text_bound_lst.append(tag)
          except:
            pass

        self.tags.append(text_bound_lst)
    self.tokenizer = tokenizer

  def process(self) -> Tuple[List[List[str]], List[List[str]]]:
    input_texts = []
    input_labels = []

    for idx in range(self.num_samples):
      full_text = self.texts[idx] # đọc dữ liệu text
      tags = self.tags[idx] # đọc dữ liệu tag (annotation)

      label_offset = []
      continuous_label_offset = []

      for tag in tags:
        offset = list(range(int(tag["start"]), int(tag["end"]) + 1))
        label_offset.append(offset)
        continuous_label_offset.append(offset)

      all_offset = list(range(len(full_text))) # tất cả các vị trí đoạn fulltext
      zero_offset = [offset for offset in all_offset if offset not in continuous_label_offset]
      # "zero_offset" danh sách chưa vị trí các từ không phải name entity

      # mục đích đoạn code dưới: nhóm các vị trí liên tiếp trong danh sách thành các khoảng liên tục (ranges)
      # Ví dụ --- Input: [1, 2, 3, 7, 8, 9, 15] --- Output: [[1, 3], [7, 9], [15, 15]]
      # "find_countinuous_ranges" hàm này sẽ được chỉnh sửa để phù hợp với yêu cầu của bài toán
      zero_offset = Preprocessing_Maccrobat.find_continuous_ranges(zero_offset)

      self.tokens = [] # sẽ được sử dụng trong hàm self._merge_offset
      self.labels = [] # sẽ được sử dụng trong hàm self._merge_offset
      self._merge_offset(full_text, tags, zero_offset, label_offset)
      assert len(self.tokens) == len(self.labels), f"Length of tokens and lables are not equal"

      input_texts.append(self.tokens)
      input_labels.append(self.labels)

    return input_texts, input_labels


  def _merge_offset(self, full_text, tags, zero_offset, label_offset):
    i = j = 0
    while i < len(zero_offset) and j < len(label_offset):
      if zero_offset[i][0] < label_offset[j][0]:
        self._add_zero(full_text, zero_offset, i)
        i += 1
      else:
        self._add_label(full_text, label_offset, j, tags)
        j += 1

    while i < len(zero_offset):
        self._add_zero(full_text, zero_offset, i)
        i += 1

    while j < len(label_offset):
        self._add_label(full_text, label_offset, j, tags)
        j += 1

  def _add_zero(self, full_text, offset, index):
    start, *_, end = offset[index] if len(offset[index]) > 1 else (offset[index][0], offset[index][0] + 1)
    text = full_text[start:end+1]
    text_tokens = self.tokenizer.tokenize(text)

    self.tokens.extend(text_tokens)
    self.labels.extend(["O"] * len(text_tokens))

  def _add_label(self, full_text, offset, index, tags):
    start, *_, end = offset[index] if len(offset[index]) > 1 else (offset[index][0], offset[index][0] +1)
    text = full_text[start:end+1]
    text_tokens = self.tokenizer.tokenize(text)

    self.tokens.extend(text_tokens)
    self.labels.extend([f"B-{tags[index]['label']}"] + [f"I-{tags[index]['label']}"] * (len(text_tokens) - 1))
    label = tags[index]["label"]

  @staticmethod
  def build_label2id(tokens: List[List[str]]):
    label2id = {}
    id_counter = 0
    # Tạo ra một danh sách phẳng (flattened list) từ danh sách lồng nhau
    for token in [token for sublist in tokens for token in sublist]:
        if token not in label2id:
          label2id[token] = id_counter
          id_counter += 1
    return label2id

  @staticmethod
  def find_continuous_ranges(data: List[int]) -> List[List[int]]:
    if not data:
        return []
    ranges = []
    start = data[0]
    prev = data[0]
    for number in data[1:]:
        if number != prev + 1:
            ranges.append(list(range(start, prev + 1)))
            start = number
        prev = number
    ranges.append(list(range(start, prev + 1)))
    return ranges


####  Giải thích đoạn code

``` python
    self.tags: List[Dict[str, str]] = []
    for i in range(self.num_samples):
      file_path = os.path.join(dataset_folder, self.ann_files[i])
      with open (file_path, "r") as f:
        text_bound_ann = [t.split("\t") for t in f.read().split("\n") if t.startswith("T")]
```

      


**1. Đọc từng dòng:**

```f.read()``` sẽ đọc toàn bộ nội dung file và chia nó thành từng dòng bằng ```.split("\n")```.
Kết quả sau ```.split("\n")```:
``` python
[
    "T1    Age 8 19    28-year-old",
    "T2    History 20 38    previously healthy",
    "T3    Sex 39 42    man",
    "T4    Clinical_event 43 52    presented",
    "E1    Clinical_event:T4"
]
```
\\
**2. Lọc các dòng bắt đầu bằng "T":**

if ```t.startswith("T")``` sẽ chỉ giữ lại các dòng bắt đầu bằng "T" (thực thể).
Dòng "E1 Clinical_event:T4" sẽ bị loại bỏ vì nó không bắt đầu bằng "T".
Kết quả sau khi lọc:
``` python
[
    "T1    Age 8 19    28-year-old",
    "T2    History 20 38    previously healthy",
    "T3    Sex 39 42    man",
    "T4    Clinical_event 43 52    presented"
]
```
\\
**3. Tách thông tin từng dòng bằng ký tự tab (\t):**

```t.split("\t")``` sẽ chia mỗi dòng thành danh sách các phần tử nhỏ hơn:

* ```"T1 Age 8 19 28-year-old" -> ["T1", "Age 8 19", "28-year-old"]```
* ```"T2 History 20 38 previously healthy" -> ["T2", "History 20 38", "previously healthy"]```
* ```"T3 Sex 39 42 man" -> ["T3", "Sex 39 42", "man"]```
* ```"T4 Clinical_event 43 52 presented" -> ["T4", "Clinical_event 43 52", "presented"].``` \\

Kết quả cuối cùng của text_bound_ann:
``` python
[
    ["T1", "Age 8 19", "28-year-old"],
    ["T2", "History 20 38", "previously healthy"],
    ["T3", "Sex 39 42", "man"],
    ["T4", "Clinical_event 43 52", "presented"]
]
```



### Giải thích đoạn code dưới đây
``` python
1 def _merge_offset(self, full_text, tags, zero_offset, label_offset):
2     i = j = 0
3     while i < len(zero_offset) and j < len(label_offset):
4      if zero_offset[i][0] < label_offset[j][0]:
5        self._add_zero(full_text, zero_offset, i)
6        i += 1
7      else:
8        self._add_label(full_text, label_offset, j, tags)
9        j += 1
10
11    while i < len(zero_offset):
12       self._add_zero(full_text, zero_offset, i)
13       i += 1
14
15    while j < len(label_offset):
16       self._add_label(full_text, label_offset, j, tags)
17       j += 1
```




**Đoạn code 3:**
``` python
    while i < len(zero_offset) and j < len(label_offset):
```
* **Ý nghĩa:**
  * Lặp qua cả hai danh sách ```zero_offset``` và ```label_offset``` đồng thời.
  * Dừng khi tất cả các khoảng trong một trong hai danh sách đã được xử lý. \\




**Đoạn code 4-6:**
``` python
if zero_offset[i][0] < label_offset[j][0]:
    self._add_zero(full_text, zero_offset, i)
    i += 1
```
* **Ý nghĩa:**

  * Kiểm tra nếu vị trí bắt đầu của ```zero_offset[i]``` nhỏ hơn vị trí bắt đầu của ```label_offset[j]```.
  * Nếu đúng: \\
Gọi hàm _add_zero để xử lý khoảng không thuộc thực thể (zero_offset).
Tăng chỉ số i để tiếp tục với khoảng zero_offset tiếp theo. \\
* **Ví dụ:**

  * ```zero_offset[i] = [0, 7]``` (tương ứng với "CASE: A").
  * ```label_offset[j] = [8, 19]``` (tương ứng với thực thể Age - "28-year-old").
  * ```0 < 8``` → Gọi ```_add_zero``` để xử lý khoảng ```[0, 7]```.



**Đoạn code 7-9:**
``` python
else:
    self._add_label(full_text, label_offset, j, tags)
    j += 1
```
* **Ý nghĩa:**

  * Nếu vị trí bắt đầu của ```label_offset[j]``` nhỏ hơn hoặc bằng vị trí bắt đầu của ```zero_offset[i]```.
  * Gọi hàm ```_add_label``` để xử lý khoảng thuộc thực thể (```label_offset```).
  * Tăng chỉ số ```j``` để tiếp tục với khoảng ```label_offset``` tiếp theo.
* **Ví dụ:**

  * ```zero_offset[i] = [43, 53]``` (khoảng không thuộc thực thể sau presented).
  * ```label_offset[j] = [8, 19]``` (thực thể Age).
  * ```43 > 8``` → Gọi _add_label để xử lý thực thể "28-year-old".



**Đoạn code 10-13:**
```python
while i < len(zero_offset):
    self._add_zero(full_text, zero_offset, i)
    i += 1
```
* **Ý nghĩa:**

  * Xử lý tất cả các khoảng còn lại trong ```zero_offset``` nếu ```label_offset``` đã hết.
* **Ví dụ:**

  * Nếu ```zero_offset = [[53, 60]]``` còn lại, nó sẽ được xử lý bởi ```_add_zero```.



**Đoạn code 14-17:**
```python
while j < len(label_offset):
    self._add_label(full_text, label_offset, j, tags)
    j += 1
```
* **Ý nghĩa:**

  * Xử lý tất cả các khoảng còn lại trong ```label_offset``` nếu ```zero_offset``` đã hết.
Ví dụ:

  * Nếu ```label_offset = [[20, 38]]``` còn lại, nó sẽ được xử lý bởi ```_add_label```.

### Preprocessing

In [ ]:
# preprocessing
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
dataset_folder = "/content/MACCROBAT2018"

Maccrobat_builder = Preprocessing_Maccrobat(dataset_folder, tokenizer)
input_texts, input_labels = Maccrobat_builder.process()
label2id = Preprocessing_Maccrobat.build_label2id(input_labels)
id2label = {v: k for k, v in label2id.items()}

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/373 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1027 > 512). Running this sequence through the model will result in indexing errors


In [ ]:
print(input_texts)
print(input_labels)

[['a', '42', '-', 'year', '-', 'old', 'woman', 'presented', 'with', 'a', 'right', 'breast', 'lump', ',', 'lower', 'back', 'pain', ',', 'loss', 'of', 'height', ',', 'marked', 'ky', '##ph', '##osis', 'and', 'he', '##pa', '##tom', '##ega', '##ly', '.', 'core', 'bio', '##ps', '##ies', 'from', 'the', 'breast', 'lump', 'showed', 'duct', '##al', 'car', '##cino', '##ma', 'in', 'situ', '(', 'sample', 'labelled', 'p', '##1', '.', '1', ';', 'supplementary', 'fig', '.', '1', 'and', 'supplementary', 'table', '1', ')', '.', 'an', 'additional', 'bio', '##psy', 'from', 'an', 'ip', '##sil', '##ater', '##al', 'ax', '##illa', '##ry', 'l', '##ym', '##ph', 'node', '(', 'p', '##1', '.', '2', ')', 'revealed', 'meta', '##static', 'duct', '##al', 'aden', '##oca', '##rc', '##ino', '##ma', '(', 'er', '+', '(', '8', '/', '8', ')', 'and', 'her', '##2', '+', '(', '3', '+', ')', ')', '.', 'computed', 'tom', '##ography', 'scan', 'revealed', 'widespread', 'meta', '##static', 'disease', 'in', 'bones', ',', 'pl', '##eur

In [ ]:
# split data
# Split
from sklearn.model_selection import train_test_split

inputs_train, inputs_val, labels_train, labels_val = train_test_split(
    input_texts,
    input_labels,
    test_size=0.2,
    random_state=42
)


In [ ]:
# Dataloader
import torch
from torch.utils.data import Dataset

MAX_LEN = 512

class NER_Dataset(Dataset):
    def __init__(self, input_texts, input_labels, tokenizer, label2id, max_len=MAX_LEN):
        super().__init__()
        self.tokens = input_texts
        self.labels = input_labels
        self.tokenizer = tokenizer
        self.label2id = label2id
        self.max_len = max_len

    def __len__(self):
        return len(self.tokens)

    def __getitem__(self, idx):
        input_token = self.tokens[idx]
        label_token = [self.label2id[label] for label in self.labels[idx]]

        input_token = self.tokenizer.convert_tokens_to_ids(input_token)
        attention_mask = [1] * len(input_token)

        input_ids = self.pad_and_truncate(input_token, pad_id=self.tokenizer.pad_token_id)
        labels = self.pad_and_truncate(label_token, pad_id=0)
        attention_mask = self.pad_and_truncate(attention_mask, pad_id=0)

        return {
            "input_ids": torch.as_tensor(input_ids),
            "labels": torch.as_tensor(labels),
            "attention_mask": torch.as_tensor(attention_mask)
        }

    def pad_and_truncate(self, inputs: list, pad_id: int):
        if len(inputs) < self.max_len:
            padded_inputs = inputs + [pad_id] * (self.max_len - len(inputs))
        else:
            padded_inputs = inputs[:self.max_len]
        return padded_inputs

    def label2id(self, labels : List [str ]):
        return [self.label2id[label] for label in labels]

train_set = NER_Dataset(inputs_train, labels_train, tokenizer, label2id)
val_set = NER_Dataset(inputs_val, labels_val, tokenizer, label2id)

In [ ]:
# modelling
from transformers import AutoModelForTokenClassification

label2id = Preprocessing_Maccrobat.build_label2id(input_labels)
id2label = {v: k for k, v in label2id.items()}

model = AutoModelForTokenClassification.from_pretrained(
    "d4data/biomedical-ner-all",
    label2id=label2id,
    id2label=id2label,
    ignore_mismatched_sizes=True
)

config.json:   0%|          | 0.00/5.00k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/266M [00:00<?, ?B/s]

Some weights of DistilBertForTokenClassification were not initialized from the model checkpoint at d4data/biomedical-ner-all and are newly initialized because the shapes did not match:
- classifier.bias: found shape torch.Size([84]) in the checkpoint and torch.Size([83]) in the model instantiated
- classifier.weight: found shape torch.Size([84, 768]) in the checkpoint and torch.Size([83, 768]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
!pip install evaluate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 38.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 15.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 20.4 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torch 2.5.1+cu124 requires nvidia-cublas-cu12==12.4.5.8; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cublas-cu12 12.5.3.2 which is incompatib

In [ ]:
# metric
import evaluate
import numpy as np

accuracy = evaluate.load("accuracy")

def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    mask = labels != 0
    predictions = np.argmax(predictions, axis=-1)
    return accuracy.compute(predictions=predictions[mask], references=labels[mask])


In [ ]:
# train_model
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(
    output_dir="./results",
    learning_rate=1e-4,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=20,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    optim="adamw_torch"
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_set,
    eval_dataset=val_set,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

trainer.train()


/usr/local/lib/python3.11/dist-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
<ipython-input-10-5d616945e48d>:16: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: nguyenanhtienbk1996 (nguyenanhtienbk1996-AAA) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


TrainOutput(global_step=200, training_loss=0.2501336669921875, metrics={'train_runtime': 348.5103, 'train_samples_per_second': 9.182, 'train_steps_per_second': 0.574, 'total_flos': 418702245888000.0, 'train_loss': 0.2501336669921875, 'epoch': 20.0})